In [1]:
from IPython.display import display, Image
import pandas as pd
import requests
import json
import csv
import geopandas as gpd
from shapely.geometry import Point
import os
import glob
import numpy as np
from shapely.wkt import loads as load_wkt

from bokeh.plotting import figure, show, gmap
from bokeh.models.mappers import LinearColorMapper
from bokeh.palettes import viridis
from bokeh.models import ColumnDataSource, GMapOptions
from bokeh.io import output_notebook

from config import (
    FS_ACCOUNTS,
    CENSUS_API_KEY,
    GOOGLE_API
)


output_notebook()


Loading BokehJS ...

# US Census Data

In [11]:
# Import all train and test independent variables
train_data = pd.read_csv('../data/raw/train.csv')
test_data = pd.read_csv('../data/raw/test.csv')
variables = ['id', 'latitude', 'longitude', 'city']
all_lat_long = pd.concat([train_data[variables], test_data[variables]])
display(all_lat_long.shape[0])

99569

In [12]:
state_dict = {
    'NYC': '36',
    'SF': '06',
    'DC': '11',
    'LA': '06',
    'Chicago': '17',
    'Boston': '25'
}
api_key = CENSUS_API_KEY
variable = 'B25064_001E'
variable_name = 'mean_gross_rent'
#'B25064_001E' --> mean gross rent -- mean_gross_rent
#'B08135_001E'--> aggregate time to work (transportation) --> time_to_work
#'B19013_001E' --> median household income --> median_household_income

In [13]:
for city_state in state_dict.items():
    city_name = city_state[0]
    state = city_state[1]
    file = '../data/processed/{}_{}.csv'.format(variable_name, city_name.lower().replace(' ','_'))
    print('########## Starting run for {}'.format(city_name))
    
    # Pulling data from the US census
    if os.path.exists(file) == False:
        url = 'https://api.census.gov/data/2018/acs/acs5?get={}&for=tract:*&in=state:{}&key={}'.format(variable, state, api_key)
        response = requests.get(url)
        rent_tract = pd.DataFrame(
            json.loads(response.text), 
            columns=[variable_name, 'state', 'county', 'tract']
        ).drop(0)

        # Reading shapefiles for tracts
        tract_geo = gpd.read_file('../data/raw/cb_2018_{}_tract_500k/'.format(state))
        tract_geo = tract_geo.merge(rent_tract, left_on=['TRACTCE', 'COUNTYFP'], right_on=['tract', 'county'], how='left')

        # Filtering aibnb data for a specific city
        city_data = all_lat_long.loc[all_lat_long.city == city_name]
        city_data = city_data.assign(geometry = [Point(x,y) for (x,y) in zip(city_data.longitude, city_data.latitude)])
        city_geo = gpd.GeoDataFrame(city_data, crs={'init': 'epsg:4326'})
        city_geo = city_geo.to_crs(tract_geo.crs)
        city_obs = city_geo.shape[0]

        # Sjoin to assign rent variable to airbnb lat/long
        city_gross_rent = gpd.sjoin(tract_geo, city_geo, how='right', op='contains')
        after_merge_obs = city_gross_rent.shape[0]
        if city_obs == after_merge_obs:
            print('All good!')
        else:
            print('Error. Before:{}, after:{}'.format(str(city_obs), str(after_merge_obs)))

        # Export to df
        export_vars = ['id', 'state','county','tract',variable_name]
        city_gross_rent[export_vars].to_csv(
            file,
            index=False
        )
    else:
        print('File already exists')

########## Starting run for NYC
All good!
########## Starting run for SF
All good!
########## Starting run for DC
All good!
########## Starting run for LA
All good!
########## Starting run for Chicago
All good!
########## Starting run for Boston
All good!


In [14]:
all_files = glob.glob('../data/processed/{}*'.format(variable_name))
all_file = '../data/processed/{}_all.csv'.format(variable_name)
try:
    all_files.remove(all_file)
except:
    print('No "all" file')
rent_var = []
for file in all_files:
    rent_var.append(pd.read_csv(file))
    os.remove(file)

rent_var = pd.concat(rent_var)
rent_var.loc[rent_var[variable_name] == -666666666, variable_name] = np.nan

display(rent_var.shape)
display(rent_var.loc[rent_var.isnull().any(axis=1)].shape)

rent_var.to_csv('../data/processed/{}_all.csv'.format(variable_name),
                index=False
               )

## Map

In [33]:
data = pd.read_csv('../data/processed/{}_all.csv'.format(variable_name))
display(data.shape[0])

99569

In [10]:
geoid_centroids = pd.read_csv(
    '../data/processed/only_airbnb_tracts_centroids.csv',
    dtype={'GEOID': str}
)
airbnb_id_to_geoid = pd.read_csv(
    '../data/processed/geoid_to_airbnb_id.csv',
    dtype={'GEOID': str}
)

In [12]:
data_geoid = data.merge(
    airbnb_id_to_geoid, how='left', on='id'
).merge(
    geoid_centroids, how='left', on='GEOID'
)

In [19]:
# Check erros by location
test_ds = ColumnDataSource(data_geoid)
mapper = LinearColorMapper(
    palette=viridis(256),
    low=data_geoid[variable_name].min(),
    high=data_geoid[variable_name].max()
)
map_options = GMapOptions(lat=37.774, lng=-122.431, map_type="roadmap", zoom=5)
p = gmap(GOOGLE_API, map_options, title=variable_name.replace('_', ' '))
p.circle('longitude', 'latitude',
         source=test_ds,
         size=20,
         alpha=0.5,
         fill_color={"field":variable_name, "transform":mapper}
        )
show(p)

# Foursquare

We find all tracts that have an airbnb listing in them and then look for their centroids

In [1]:
# state_dict = {
#     'NYC': '36',
#     'SF': '06',
#     'DC': '11',
#     'LA': '06',
#     'Chicago': '17',
#     'Boston': '25'
# }
# # Import all train and test independent variables
# train_data = pd.read_csv('../data/raw/train.csv')
# test_data = pd.read_csv('../data/raw/test.csv')
# variables = ['id', 'latitude', 'longitude', 'city']
# all_lat_long = pd.concat([train_data[variables], test_data[variables]])

# all_geoid_to_id = []
# all_unique_airbnb_tracts = []
# for city_state in state_dict.items():
#     city_name = city_state[0]
#     state = city_state[1]
#     print('########## Starting run for {}'.format(city_name))
#     tract_geo = gpd.read_file('../data/raw/cb_2018_{}_tract_500k/'.format(state))

#     city_data = all_lat_long.loc[all_lat_long.city == city_name]
#     city_data = city_data.assign(geometry = [Point(x,y) for (x,y) in zip(city_data.longitude, city_data.latitude)])
#     city_geo = gpd.GeoDataFrame(city_data, crs={'init': 'epsg:4326'})
#     city_geo = city_geo.to_crs(tract_geo.crs)

#     tracts_in_airbnb = gpd.sjoin(tract_geo, city_geo, how='inner', op='contains')
#     geoid_to_id = tracts_in_airbnb[['GEOID', 'id']]
#     tracts_in_airbnb = tracts_in_airbnb.drop(['index_right', 'id', 'latitude', 'longitude'], axis=1)
#     tracts_in_airbnb = tracts_in_airbnb.drop_duplicates()
#     tracts_in_airbnb = tracts_in_airbnb.assign(
#         area = tracts_in_airbnb.geometry.map(lambda x: x.area),
#         centroid = tracts_in_airbnb.geometry.map(lambda x: x.centroid)
#     )
#     all_geoid_to_id.append(geoid_to_id)
#     all_unique_airbnb_tracts.append(tracts_in_airbnb)

# all_geoid_to_id = pd.concat(all_geoid_to_id)
# all_unique_airbnb_tracts = pd.concat(all_unique_airbnb_tracts)

# all_unique_airbnb_tracts = all_unique_airbnb_tracts.assign(
#     longitude = all_unique_airbnb_tracts.centroid.map(lambda x: x.x),
#     latitude = all_unique_airbnb_tracts.centroid.map(lambda x: x.y)
# )

# all_geoid_to_id.to_csv('../data/processed/geoid_to_airbnb_id.csv',
#                        index=False,
#                        quoting=csv.QUOTE_ALL
#                       )

# all_unique_airbnb_tracts[['GEOID', 'longitude', 'latitude']].to_csv(
#     '../data/processed/only_airbnb_tracts_centroids.csv',
#     index=False,
#     quoting=csv.QUOTE_ALL
# )

We query foursquare information for each centroid

In [2]:
query_coords = pd.read_csv('../data/processed/only_airbnb_tracts_centroids.csv',
                           dtype={'GEOID': str}
                          )

fs_categories = {
    'historic_site': '4deefb944765f83613cdba6e',
    'art_museum': '4bf58dd8d48988d18f941735',
    'history_museum': '4bf58dd8d48988d190941735',
    'planetarium': '4bf58dd8d48988d192941735',
    'science_museum': '4bf58dd8d48988d191941735',
    'opera_house': '4bf58dd8d48988d136941735',
    'theater': '4bf58dd8d48988d137941735',
    'outdoor_sculpture': '52e81612bcbc57f1066b79ed',
    'street_art': '52e81612bcbc57f1066b79ee',
    'zoo': '4bf58dd8d48988d17b941735',
    'city_hall': '4bf58dd8d48988d129941735',
}
category_ids = ','.join(fs_categories.values())
version = '20200914'
radius = 700
failed_geoid_file = '../data/interim/fs_data/turistic_sites_700m/failed_geoid.txt'
url = "https://api.foursquare.com/v2/venues/search"

accounts = FS_ACCOUNTS
n_account = 0

# Restarting the failed file
with open(failed_geoid_file, 'w') as outfile:
    json.dump([], outfile)

def append_failed_run(failed_geoid_file, geoid):
    with open(failed_geoid_file) as json_file:
        failed_geoids = json.load(json_file)
    failed_geoids.append(geoid)
    with open(failed_geoid_file, 'w') as outfile:
        json.dump(failed_geoids, outfile)

for i,coord in enumerate(query_coords.itertuples()):
    valid_account = accounts[n_account]
    client_id = valid_account['client_id']
    client_secret = valid_account['client_secret']
    geoid = coord.GEOID
    lat = coord.latitude
    long = coord.longitude
    geoid_out_file = '../data/interim/fs_data/turistic_sites_700m/{}.txt'.format(geoid)
    if os.path.exists(geoid_out_file) == False:
        print('####### {}. Starting request for GEOID {}'.format(i, geoid))
        lat_long = '{},{}'.format(str(lat), str(long))
        params = {
            'client_id': client_id,
            'client_secret': client_secret,
            'll': lat_long,
            'radius':radius,
            'limit':50,
            'categoryId':category_ids,
            'v': version
        }

        response = requests.get(url, params=params)
        if response.status_code == 200: 
            response_json = json.loads(response.text)
            with open(geoid_out_file, 'w') as outfile:
                json.dump(response_json, outfile)
            print('Success')
        elif (response.status_code == 429) & (n_account + 1 < len(accounts)):
            n_account += 1
            valid_account = accounts[n_account]
            params['client_id'] = valid_account['client_id']
            params['client_secret'] = valid_account['client_secret']
            response = requests.get(url, params=params)
            if response.status_code == 200: 
                response_json = json.loads(response.text)
                with open(geoid_out_file, 'w') as outfile:
                    json.dump(response_json, outfile)
                print('Changed key, success')
            else:
                print('Failed, status code: {}'.format(str(response.status_code)))
                append_failed_run(failed_geoid_file, geoid)
        elif (n_account + 1 >= len(accounts)):
            break
        else:
            print('Failed, status code: {}'.format(str(response.status_code)))
            append_failed_run(failed_geoid_file, geoid)
    else:
        print('####### {}. Request for GEOID {} already exists'.format(i,geoid))

all_files = glob.glob('../data/interim/fs_data/turistic_sites_700m/*')
all_files.remove(failed_geoid_file)
all_fs_data = []

for i, file in enumerate(all_files):
    print(i)
    geoid = file.replace('../data/interim/fs_data/turistic_sites_700m/','').replace('.txt','')
    # Parse jsons
    with open(file) as json_file:
        geoid_json = json.load(json_file)
    all_venues = geoid_json['response']['venues']
    for venue_data in all_venues:
        parsed_venue = {}
        parsed_venue['id'] = venue_data['id']
        location = venue_data.get('location', np.nan)
        if location != np.nan:
            parsed_venue['lat'] = location.get('lat', np.nan)
            parsed_venue['lng'] = location.get('lng', np.nan)
            parsed_venue['distance'] = location.get('distance', np.nan)
            parsed_venue['postal_code'] = location.get('postalCode', np.nan)
            parsed_venue['city'] = location.get('city', np.nan)
            parsed_venue['state'] = location.get('state', np.nan)
        categories = venue_data.get('categories', np.nan)

        for cat in categories:
            cat_ids = []
            cat_name = []
            cat_ids.append(cat['id'])
            cat_name.append(cat['name'])

        parsed_venue['cat_ids'] = ','.join(cat_ids)
        parsed_venue['cat_names'] = ','.join(cat_name)
        parsed_venue['geoid'] = geoid

        df_res = pd.DataFrame(parsed_venue, index=[0])
        all_fs_data.append(df_res)

all_fs_data = pd.concat(all_fs_data)
all_fs_data.to_csv('../data/processed/fs_data_turistic700m_geoid.csv',
                   index=False
                  )

all_fs_data = pd.read_csv(
    '../data/processed/fs_data_turistic700m_geoid.csv',
    dtype={'geoid':str}
                         )
fs_agg_data = all_fs_data.groupby(['geoid']).agg({'id':'count'}).reset_index()
fs_agg_data = fs_agg_data.rename(columns={
    'geoid': 'GEOID',
    'id': 'total'
})

In [18]:
filter_cats = [
    'Park', 
    'Art Gallery', 'Theater', 'Historic Site',
    'General Entertainment','Performing Arts Venue', 'Concert Hall',
    'History Museum', 'Indie Theater', 'Museum',
    'Public Art'
]
fs_agg_data = fs_agg_data.loc[fs_agg_data.cat_names.isin(filter_cats)]

In [22]:
geoid_to_id = pd.read_csv(
    '../data/processed/geoid_to_airbnb_id.csv',
    dtype={'GEOID': str}
)
display(geoid_to_id.shape[0])

geoid_to_id_m = geoid_to_id.merge(fs_agg_data, how='left')

# geoid_to_id_m = geoid_to_id_m.pivot_table(index='id', columns='cat_names', values='total', fill_value=0).reset_index()
# geoid_to_id_m.columns = [column.lower().replace(' ','_') for column in geoid_to_id_m.columns]
geoid_to_id = geoid_to_id.merge(geoid_to_id_m, how='left')
geoid_to_id = geoid_to_id.fillna(0)

all_cols = list(geoid_to_id.columns)
all_cols.remove('id')
geoid_to_id = geoid_to_id.assign(total_entertainment = geoid_to_id[all_cols].sum(axis=1))

# geoid_to_id = geoid_to_id.rename(columns={'total':'total_turism'})

geoid_to_id.to_csv('../data/processed/fs_agg_data_airbnb_id_turism700m.csv',
                   index=False
                  )

99513

# Parks

Parks data from https://www.openicpsr.org/openicpsr/project/117921/version/V1/view;jsessionid=13FE4BEB13A399EE9C3F81CCD9C5ABD9?path=/openicpsr/117921/fcr:versions/V1.1/nanda_parks_tract_2018_01P_csv_with_readme.zip&type=file

In [29]:
parks = pd.read_csv(
    '../data/raw/nanda_parks_tract_2018_01P.csv',
    dtype={'tract_fips10':str}
)
geoid_to_id = pd.read_csv(
    '../data/processed/geoid_to_airbnb_id.csv',
    dtype={'GEOID': str}
)

In [25]:
parks = parks[['tract_fips10', 'count_open_parks']]
parks = parks.rename(
    columns={'tract_fips10': 'GEOID'}
)
parks_id = geoid_to_id.merge(parks, on='GEOID', how='left')

In [28]:
parks_id.to_csv(
    '../data/processed/parks_in_tract.csv',
    index=False
)